In [2]:
function filename_splitter(filename::String)
    
    fn_splitted = split(filename, "_")

    nozzle_RR = parse(Float64, fn_splitted[end-3][1:end-4])
    surftemp  = parse(Float64, fn_splitted[end-1][1:end-1])

    return nozzle_RR, surftemp
end;

In [43]:
using Parameters

include("function_convert_and_process.jl")
include("TPX3_analysis_structs.jl")
version    = "1.0.0"
parameters = pars()

parameters.data_path      = "C:/Users/BeamER-C/timepix3 analysis/Data/15.05.2024"

filename                  = "011_Ptright_lower_1prcO2_600V_100Hz_100us_10HzD2_100kHz_260C_000000"
parameters.filename_stem  = parameters.data_path * "/" * filename

#-------------------------------------------------------------------#
#-----------------        PARAMETER SECTION        -----------------#

parameters.write_bin      = false
parameters.write_txt      = false

parameters.mode           = 3
parameters.first_seconds  = 3

parameters.mode3_t0       = 50
parameters.mode3_tmax     = 300

# TOF Parameters
parameters.tof_max        = 10e-6
parameters.tof_bin        = 10e-9
parameters.tof_gates      = [4.11, 4.28] .* 1e-6 # must be sorted!

# Image Parameters 
parameters.create_image   = true
parameters.image_x_laser  = 106
parameters.image_y_laser  = 142
parameters.image_x_offset = 5
parameters.image_y_offset = 0
parameters.image_x_width  = 50
parameters.image_y_width  = 40

# Incident Beam Parameters
parameters.beam_x_min     = 68
parameters.beam_x_max     = 95
parameters.beam_y_min     = 150
parameters.beam_y_max     = 180
parameters.beam_zscale    = 100

# Kinetic Trace create parameters
parameters.kt_max         = 1/filename_splitter(filename)[1]
parameters.kt_bin         = 10e-6
parameters.kt_nbins       = Int(floor(parameters.kt_max/parameters.kt_bin))
parameters.kt_length      = 1000
parameters.t_noz_laser    = 165.7e-6
parameters.t_laser_surf   = 7e-6

# Detect Signal in Real Time, not correlated with beam shots
parameters.realtime       = true
parameters.realtime_t0    = 0
parameters.realtime_bin   = 1e0
parameters.realtime_tmax  = 2000

# Laser and nozzle frequencies (Hz)
parameters.freq_nozzle    = filename_splitter(filename)[1]
parameters.freq_laser     = 10e3
parameters.chunk_size     = (800*1024*1024)÷8

println("selected file\t: ", filename)
BGhists, x_tof, tof_spec, x_kt, traces, traces_bg, rt_sig, rt_bg, time_exp = convert_and_process(parameters);

selected file	: 011_Ptright_lower_1prcO2_600V_100Hz_100us_10HzD2_100kHz_260C_000000
filesize	: 1.98 GB
------------------------------------------------------------------------------------------
Start processing file
------------------------------------------------------------------------------------------
getting initial chunk
	 beam times in this chunk: 0.016737951 - 118.92704 seconds
getting chunk number 2
	 beam times in this chunk: 118.92704 - 237.13728 seconds
getting chunk number 3
	 beam times in this chunk: 237.13728 - 300.14276 seconds

done converting data

------------------------------------------------------------------------------------------
Processing time
	Absolute: 52.3	seconds
	Relative: 0.44	min/GB
Total exp. time	: 300.1	seconds
------------------------------------------------------------------------------------------


In [247]:
pRGAmz  = 3.23e-12
freqS1  = 12.5
US1     = 400
dtS1    = 50
tTitr   = parameters.mode3_tmax
prcO2   = 100
pGP     = 0

# ------------------------------------------------------------------------------------- #
exp_header = 
[
["# measurement type: ",            "D2 Oxidation - RRR Experiment" ], # 
["# surface: ",                     "Pt(111)" ],
["# surface temperature [°C]: ",    filename_splitter(filename)[2] ],
["# p(Granv. Phil.) [mbar]: ",      0 ],
["# p(RGA, m/z=32) [Torr]: ",       pRGAmz ],
["# percentage O2 in beam [%]: ",   prcO2 ],
["# start time titration [s]: ",    tTitr ],
["# freq. S2 [Hz]: ",               filename_splitter(filename)[1]],
["# freq. S1 [Hz]: ",               freqS1 ],
["# voltage S1 [V]: ",              US1 ],
["# opening time S1 [µs]: "         dtS1 ],
["# total experimental time [s]: ", time_exp],
];
include("header.jl")